In [1]:
# Import relevant modules
import pandas as pd
import numpy as np
import seaborn as sb
import matplotlib.pyplot as plt
sb.set()
import altair as alt
import os

In [2]:
# Import primary dataset
world = pd.read_csv("covid-policy-tracker/data/OxCGRT_latest.csv")
world['Date'] = pd.to_datetime(world['Date'].astype(str), format='%Y%m%d')
world.head()

CountryName CountryCode       Date  C1_School closing  C1_Flag  \
0       Aruba         ABW 2020-01-01                0.0      NaN   
1       Aruba         ABW 2020-01-02                0.0      NaN   
2       Aruba         ABW 2020-01-03                0.0      NaN   
3       Aruba         ABW 2020-01-04                0.0      NaN   
4       Aruba         ABW 2020-01-05                0.0      NaN   

   C2_Workplace closing  C2_Flag  C3_Cancel public events  C3_Flag  \
0                   0.0      NaN                      0.0      NaN   
1                   0.0      NaN                      0.0      NaN   
2                   0.0      NaN                      0.0      NaN   
3                   0.0      NaN                      0.0      NaN   
4                   0.0      NaN                      0.0      NaN   

   C4_Restrictions on gatherings  ...  StringencyIndex  \
0                            0.0  ...              0.0   
1                            0.0  ...              0.0   
2                            0.0  ...              0.0   
3                            0.0  ...              0.0   
4                            0.0  ...              0.0   

   StringencyIndexForDisplay  StringencyLegacyIndex  \
0                        0.0                    0.0   
1                        0.0                    0.0   
2                        0.0                    0.0   
3                        0.0                    0.0   
4                        0.0                    0.0   

   StringencyLegacyIndexForDisplay  GovernmentResponseIndex  \
0                              0.0                      0.0   
1                              0.0                      0.0   
2                              0.0                      0.0   
3                              0.0                      0.0   
4                              0.0                      0.0   

   GovernmentResponseIndexForDisplay  ContainmentHealthIndex  \
0                                0.0                     0.0   
1                                0.0                     0.0   
2                                0.0                     0.0   
3                                0.0                     0.0   
4                                0.0                     0.0   

   ContainmentHealthIndexForDisplay  EconomicSupportIndex  \
0                               0.0                   0.0   
1                               0.0                   0.0   
2                               0.0                   0.0   
3                               0.0                   0.0   
4                               0.0                   0.0   

   EconomicSupportIndexForDisplay  
0                             0.0  
1                             0.0  
2                             0.0  
3                             0.0  
4                             0.0  

[5 rows x 42 columns]

In [3]:
# Import secondary dataset
owidData = pd.read_csv('covid-19-data/public/data/owid-covid-data.csv')
owidData = owidData.rename(columns = {'iso_code' : 'CountryCode', 'location':'CountryName', 'date':'Date', 
                                      'new_cases':'NewCases', 'total_cases_per_million':'TotalCasesPerMillion', 
                                      'new_cases_per_million':'NewCasesPerMillion'})
owidData = owidData[['CountryCode', 'Date', 'NewCases', 'TotalCasesPerMillion', 'NewCasesPerMillion']]
owidData.Date = owidData.Date.astype('datetime64[ns]')
owidData.head()

CountryCode       Date  NewCases  TotalCasesPerMillion  NewCasesPerMillion
0         ABW 2020-03-13         2                18.733              18.733
1         ABW 2020-03-20         2                37.465              18.733
2         ABW 2020-03-24         8               112.395              74.930
3         ABW 2020-03-25         5               159.227              46.831
4         ABW 2020-03-26         2               177.959              18.733

In [4]:
# Merge DataFrames
world = world.merge(owidData, on = ['CountryCode', 'Date'], how = 'outer')

In [5]:
# Excuse the messy code here sorry 
china = world[world.CountryName == "China"]
singapore = world[world.CountryName == "Singapore"]
usa = world[world.CountryName == "United States"]
italy = world[world.CountryName == "Italy"]
skorea = world[world.CountryName == "South Korea"]
iran = world[world.CountryName == "Iran"]
taiwan = world[world.CountryName == "Taiwan"]
hk = world[world.CountryName == "Hong Kong"]
uk = world[world.CountryName == "United Kingdom"]

countries = [china, singapore, usa, italy, skorea, iran,
            taiwan, hk, uk]

countryNames = ['China', 'Singapore', 'USA', 'Italy', 'South Korea', 'Iran',
                'Taiwan', 'Hong Kong', 'United Kingdom']

In [6]:
# Plot number of cases for each country
keyCountries = pd.concat(countries)
alt.Chart(keyCountries).mark_line().encode(
    x = 'Date',
    y = 'ConfirmedCases',
    color = 'CountryName'
).interactive().properties(
    title = 'Number of Cases by Country'
)

alt.Chart(...)

In [7]:
# Plot policy stringency index of each country

alt.Chart(keyCountries).mark_line().encode(
    x = 'Date',
    y = 'StringencyIndex',
    color = 'CountryName'
).properties(
    title = 'Policy Stringency in Key Countries'
).interactive()

alt.Chart(...)

In [67]:
def caseStringency(country):
    
    source = world[world.CountryName == country]

    base = alt.Chart(source).encode(
        alt.X('Date:T')
    ).properties(
        width = 375,
        height = 275
    )

    cases = base.mark_line(color='#5276A7').encode(
        alt.Y('ConfirmedCases:Q', axis=alt.Axis(titleColor='#5276A7')),
        tooltip = 'ConfirmedCases'
    )

    stringency = base.mark_line(color='#F18727').encode(
        alt.Y('StringencyIndex:Q', axis=alt.Axis(titleColor='#F18727')),
        tooltip = 'StringencyIndex'
    )

    combined = (cases + stringency).resolve_scale(y='independent').properties(
        title = 'Confirmed Cases vs. Policy Stringency in ' + country,
    )

    return combined

In [68]:
caseStringency('China') & caseStringency('Hong Kong') \
|caseStringency('Singapore') & caseStringency('United States')

alt.HConcatChart(...)

# Strategy
---
The aim here is to find out which policies are most effective. Can try take the following steps:
1. Single out the Top 100 countries with the most cases (this is just to remove any clutter from the dataset)
2. Of the Top 100 countries with the most cases, look at the number of new cases. For the countries with less than x number of new cases per day for 14 days, single them out. Do make sure to play around with the value of x, to see how this affects the policy relation later on. We will call these countries model countries.
3. Plot the policies of these new countries on a time series, with see if there are any trends. 
4. Compare the daily means of stringency for each policy of the model countries against the rest of the dataset. 

In [10]:
# Top 100 confirmed cases countries
from datetime import datetime, timedelta
end_date = (datetime.now() - timedelta(1)).strftime('%Y-%m-%d')
latestPull = world[world.Date == end_date]
top100 = latestPull.nlargest(50, 'ConfirmedCases')
print(top100.shape)
top100.head()

(50, 45)


CountryName CountryCode       Date  C1_School closing  C1_Flag  \
23142   United States         USA 2020-05-24                NaN      NaN   
3356           Brazil         BRA 2020-05-24                NaN      NaN   
18685          Russia         RUS 2020-05-24                3.0      0.0   
8320   United Kingdom         GBR 2020-05-24                NaN      NaN   
7444            Spain         ESP 2020-05-24                NaN      NaN   

       C2_Workplace closing  C2_Flag  C3_Cancel public events  C3_Flag  \
23142                   NaN      NaN                      NaN      NaN   
3356                    NaN      NaN                      NaN      NaN   
18685                   2.0      0.0                      2.0      1.0   
8320                    NaN      NaN                      NaN      NaN   
7444                    NaN      NaN                      NaN      NaN   

       C4_Restrictions on gatherings  ...  StringencyLegacyIndexForDisplay  \
23142                            NaN  ...                            70.00   
3356                             NaN  ...                            77.62   
18685                            4.0  ...                            73.33   
8320                             NaN  ...                            72.62   
7444                             NaN  ...                            82.38   

       GovernmentResponseIndex  GovernmentResponseIndexForDisplay  \
23142                      NaN                              71.47   
3356                       NaN                              66.35   
18685                      NaN                              77.24   
8320                       NaN                              64.10   
7444                       NaN                              77.24   

       ContainmentHealthIndex  ContainmentHealthIndexForDisplay  \
23142                     NaN                             73.11   
3356                      NaN                             69.32   
18685                     NaN                             82.20   
8320                      NaN                             57.58   
7444                      NaN                             75.38   

       EconomicSupportIndex  EconomicSupportIndexForDisplay  NewCases  \
23142                   NaN                            62.5   21236.0   
3356                    NaN                            50.0   16508.0   
18685                   NaN                            50.0    9434.0   
8320                    NaN                           100.0    2959.0   
7444                    NaN                            87.5     482.0   

       TotalCasesPerMillion  NewCasesPerMillion  
23142              4902.287              64.157  
3356               1634.357              77.663  
18685              2301.595              64.645  
8320               3788.027              43.588  
7444               5042.735              10.309  

[5 rows x 45 columns]

In [11]:
# Collect data from the last 14 days (incubation period)
end_date = (datetime.now() - timedelta(1)).strftime('%Y-%m-%d')
start_date = (datetime.now() - timedelta(15)).strftime('%Y-%m-%d')
mask = (world['Date'] > start_date) & (world['Date'] <= end_date)

incubationData = world.loc[mask]
print(incubationData.shape)
incubationData.head()

(3003, 45)


CountryName CountryCode       Date  C1_School closing  C1_Flag  \
131       Aruba         ABW 2020-05-11                3.0      1.0   
132       Aruba         ABW 2020-05-12                3.0      1.0   
133       Aruba         ABW 2020-05-13                3.0      1.0   
134       Aruba         ABW 2020-05-14                3.0      1.0   
135       Aruba         ABW 2020-05-15                3.0      1.0   

     C2_Workplace closing  C2_Flag  C3_Cancel public events  C3_Flag  \
131                   2.0      1.0                      2.0      1.0   
132                   2.0      1.0                      2.0      1.0   
133                   2.0      1.0                      2.0      1.0   
134                   2.0      1.0                      2.0      1.0   
135                   2.0      1.0                      2.0      1.0   

     C4_Restrictions on gatherings  ...  StringencyLegacyIndexForDisplay  \
131                            4.0  ...                            76.43   
132                            4.0  ...                            76.43   
133                            4.0  ...                            76.43   
134                            4.0  ...                            76.43   
135                            4.0  ...                            76.43   

     GovernmentResponseIndex  GovernmentResponseIndexForDisplay  \
131                    68.59                              68.59   
132                    68.59                              68.59   
133                    68.59                              68.59   
134                    68.59                              68.59   
135                    68.59                              68.59   

     ContainmentHealthIndex  ContainmentHealthIndexForDisplay  \
131                   71.97                             71.97   
132                   71.97                             71.97   
133                   71.97                             71.97   
134                   71.97                             71.97   
135                   71.97                             71.97   

     EconomicSupportIndex  EconomicSupportIndexForDisplay  NewCases  \
131                  50.0                            50.0       0.0   
132                  50.0                            50.0       0.0   
133                  50.0                            50.0       0.0   
134                  50.0                            50.0       0.0   
135                  50.0                            50.0       0.0   

     TotalCasesPerMillion  NewCasesPerMillion  
131               945.994                 0.0  
132               945.994                 0.0  
133               945.994                 0.0  
134               945.994                 0.0  
135               945.994                 0.0  

[5 rows x 45 columns]

In [45]:
# Find the countries with the highest mean new cases in the last 14 days
mean = incubationData.groupby("CountryName").mean()
mean.nlargest(50, 'NewCasesPerMillion').head()

C1_School closing  C1_Flag  C2_Workplace closing  C2_Flag  \
CountryName                                                              
Qatar                      3.0      1.0                   2.0      1.0   
Kuwait                     3.0      1.0                   3.0      1.0   
Bahrain                    3.0      1.0                   2.0      1.0   
Chile                      3.0      1.0                   2.0      1.0   
Peru                       3.0      1.0                   3.0      1.0   

             C3_Cancel public events  C3_Flag  C4_Restrictions on gatherings  \
CountryName                                                                    
Qatar                            2.0      1.0                            4.0   
Kuwait                           2.0      1.0                            4.0   
Bahrain                          2.0      1.0                            4.0   
Chile                            2.0      1.0                            3.0   
Peru                             2.0      1.0                            4.0   

             C4_Flag  C5_Close public transport  C5_Flag  ...  \
CountryName                                               ...   
Qatar            1.0                        2.0      1.0  ...   
Kuwait           1.0                        2.0      1.0  ...   
Bahrain          1.0                        1.0      1.0  ...   
Chile            1.0                        0.0      NaN  ...   
Peru             1.0                        2.0      1.0  ...   

             StringencyLegacyIndexForDisplay  GovernmentResponseIndex  \
CountryName                                                             
Qatar                                  90.00                    76.28   
Kuwait                                 97.14                    87.82   
Bahrain                                85.24                    82.69   
Chile                                  76.43                    71.15   
Peru                                   97.14                    87.18   

             GovernmentResponseIndexForDisplay  ContainmentHealthIndex  \
CountryName                                                              
Qatar                                    76.28                   83.33   
Kuwait                                   87.82                   96.97   
Bahrain                                  82.69                   81.82   
Chile                                    71.15                   77.27   
Peru                                     87.18                   89.39   

             ContainmentHealthIndexForDisplay  EconomicSupportIndex  \
CountryName                                                           
Qatar                                   83.33                  37.5   
Kuwait                                  96.97                  37.5   
Bahrain                                 81.82                  87.5   
Chile                                   77.27                  37.5   
Peru                                    89.39                  75.0   

             EconomicSupportIndexForDisplay     NewCases  \
CountryName                                                
Qatar                                  37.5  1491.571429   
Kuwait                                 37.5   917.214286   
Bahrain                                87.5   287.714286   
Chile                                  37.5  2726.714286   
Peru                                   75.0  3624.214286   

             TotalCasesPerMillion  NewCasesPerMillion  
CountryName                                            
Qatar                11085.230571          517.716214  
Kuwait                3369.010429          214.776143  
Bahrain               4029.944857          169.086286  
Chile                 2320.050429          142.638929  
Peru                  2740.572000          109.918500  

[5 rows x 42 columns]

In [13]:
# Isolate countries that have had more than 30 new cases on a single day for the last 14 days
activeCountries = []
for i in range(len(incubationData['NewCases'])):
    if incubationData["NewCases"].iloc[i] >= 50 and incubationData["CountryName"].iloc[i] not in activeCountries:
        activeCountries.append(incubationData["CountryName"].iloc[i])

print(activeCountries)
print("Active Countries: {}" .format(len(activeCountries)))

['Afghanistan', 'United Arab Emirates', 'Argentina', 'Austria', 'Azerbaijan', 'Belgium', 'Bangladesh', 'Bulgaria', 'Bahrain', 'Bosnia and Herzegovina', 'Belarus', 'Bolivia', 'Brazil', 'Central African Republic', 'Canada', 'Switzerland', 'Chile', "Cote d'Ivoire", 'Cameroon', 'Democratic Republic of Congo', 'Congo', 'Colombia', 'Czech Republic', 'Germany', 'Djibouti', 'Denmark', 'Dominican Republic', 'Algeria', 'Ecuador', 'Egypt', 'Spain', 'Ethiopia', 'Finland', 'France', 'Gabon', 'United Kingdom', 'Ghana', 'Guatemala', 'Honduras', 'Hungary', 'Indonesia', 'India', 'Ireland', 'Iran', 'Iraq', 'Italy', 'Japan', 'Kazakhstan', 'Kenya', 'Kyrgyz Republic', 'Kuwait', 'Lebanon', 'Morocco', 'Moldova', 'Mexico', 'Mongolia', 'Mauritania', 'Malaysia', 'Nigeria', 'Nicaragua', 'Netherlands', 'Norway', 'Nepal', 'Oman', 'Pakistan', 'Panama', 'Peru', 'Philippines', 'Poland', 'Puerto Rico', 'Portugal', 'Qatar', 'Romania', 'Russia', 'Saudi Arabia', 'Sudan', 'Senegal', 'Singapore', 'El Salvador', 'Somalia', 

In [14]:
world.groupby("CountryName").mean()

C1_School closing  C1_Flag  C2_Workplace closing   C2_Flag  \
CountryName                                                               
Afghanistan           1.457746    1.000              1.246479  0.000000   
Albania               1.442748    1.000              0.961832  0.000000   
Algeria               1.531034    1.000              1.041379  0.603175   
Andorra               1.415493    1.000              1.232394  1.000000   
Angola                1.182482    1.000              0.941606  1.000000   
...                        ...      ...                   ...       ...   
Venezuela             1.381295    1.000              1.381295  0.984375   
Vietnam               1.986207    0.625              1.020690  0.852459   
Yemen                 1.316547    1.000              0.000000       NaN   
Zambia                1.257353    1.000              0.250000  1.000000   
Zimbabwe              1.208633    1.000              1.079137  1.000000   

             C3_Cancel public events   C3_Flag  C4_Restrictions on gatherings  \
CountryName                                                                     
Afghanistan                 1.154930  0.792683                       1.323944   
Albania                     0.961832  1.000000                       1.358779   
Algeria                     1.048276  1.000000                       1.544828   
Andorra                     0.492958  1.000000                       0.000000   
Angola                      0.744526  1.000000                       1.467153   
...                              ...       ...                            ...   
Venezuela                   0.978417  1.000000                       1.438849   
Vietnam                     1.475862  0.542056                       1.344828   
Yemen                       0.906475  1.000000                       0.000000   
Zambia                      0.338235  0.000000                       1.294118   
Zimbabwe                    0.906475  1.000000                       1.359712   

              C4_Flag  C5_Close public transport  C5_Flag  ...  \
CountryName                                                ...   
Afghanistan  1.000000                   0.774648      0.0  ...   
Albania      1.000000                   0.900763      0.0  ...   
Algeria      0.000000                   0.868966      1.0  ...   
Andorra           NaN                   0.408451      1.0  ...   
Angola       1.000000                   0.569343      1.0  ...   
...               ...                        ...      ...  ...   
Venezuela    1.000000                   0.000000      NaN  ...   
Vietnam      0.883333                   0.593103      1.0  ...   
Yemen             NaN                   0.000000      NaN  ...   
Zambia       0.549020                   0.000000      NaN  ...   
Zimbabwe     1.000000                   0.359712      1.0  ...   

             StringencyLegacyIndexForDisplay  GovernmentResponseIndex  \
CountryName                                                             
Afghanistan                        37.305959                28.363451   
Albania                            42.423406                33.117891   
Algeria                            41.310342                28.333724   
Andorra                            34.292945                24.598451   
Angola                             37.959444                28.513869   
...                                      ...                      ...   
Venezuela                          42.814863                33.389496   
Vietnam                            55.239110                45.241103   
Yemen                              24.826575                13.027554   
Zambia                             29.721538                23.012279   
Zimbabwe                           44.213425                30.214676   

             GovernmentResponseIndexForDisplay  ContainmentHealthIndex  \
CountryName                                                              
Afghanistan               

In [15]:
countries = world["CountryName"].unique()
rcvdCountries = list(set(countries) - set(activeCountries))
print("Low Impact Countries: " + str(len(rcvdCountries)))
rcvdCountries.sort()
print(rcvdCountries)

Low Impact Countries: 78
['Albania', 'Andorra', 'Angola', 'Aruba', 'Australia', 'Barbados', 'Belize', 'Benin', 'Bermuda', 'Bhutan', 'Botswana', 'Brunei', 'Burkina Faso', 'Burundi', 'Cape Verde', 'Chad', 'China', 'Costa Rica', 'Croatia', 'Cuba', 'Cyprus', 'Dominica', 'Estonia', 'Eswatini', 'Gambia', 'Georgia', 'Greece', 'Greenland', 'Guam', 'Guyana', 'Hong Kong', 'Iceland', 'Israel', 'Jamaica', 'Jordan', 'Kosovo', 'Laos', 'Lesotho', 'Liberia', 'Libya', 'Lithuania', 'Luxembourg', 'Macao', 'Madagascar', 'Malawi', 'Mali', 'Mauritius', 'Mozambique', 'Myanmar', 'Namibia', 'New Zealand', 'Niger', 'Palestine', 'Papua New Guinea', 'Paraguay', 'Rwanda', 'San Marino', 'Seychelles', 'Sierra Leone', 'Slovak Republic', 'Slovenia', 'Solomon Islands', 'South Korea', 'Sri Lanka', 'Suriname', 'Syria', 'Taiwan', 'Tanzania', 'Thailand', 'Timor', 'Trinidad and Tobago', 'Tunisia', 'Turkmenistan', 'Uganda', 'Uruguay', 'Vietnam', 'Yemen', 'Zimbabwe']


Take Hong Kong, China, New Zealand, South Korea as positive examples

Take USA, UK, Spain, Iran as negative examples

In [44]:
# Altair function to plot closure (for now, still inefficient)
def plotClosure(country):
    
    source = world[world.CountryName == country]
    
    base = alt.Chart(source).encode(
            alt.X('Date:T')
    )
    
    closure =  base.transform_fold(
        fold = ['C1_School closing', 'C2_Workplace closing',
        'C3_Cancel public events', 'C4_Restrictions on gatherings',
        'C5_Close public transport'],
        as_ = ['Policy', 'Stringency'],
    ).mark_area(
        opacity = 0.2,
        line = True
    ).encode(
        y = alt.Y('Stringency:Q', 
                  stack = None, 
                  scale = alt.Scale(domain = [0, 4])),
        color = alt.Color('Policy:N', 
                          scale=alt.Scale(scheme='set1'),
                          legend = alt.Legend(orient='bottom')),
        tooltip = 'Policy:N'
    ).properties(
        title = 'Closure Policies in ' + country,
    )
    
    cases = base.mark_line().encode(
        y = 'ConfirmedCases'
    ).properties(
        title = 'Confirmed Cases in ' + country
    )
    
    return closure | cases

# Recovery Examples

In [43]:
# Positive examples:
plotClosure('Hong Kong') & plotClosure('China') & plotClosure('New Zealand') & plotClosure('South Korea')

alt.VConcatChart(...)

# Absolute Highest Numbers

In [41]:
# Countries with highest count of confirmed cases
alt.vconcat(plotClosure('United States'),
           plotClosure('United Kingdom'),
           plotClosure('Russia'),
           plotClosure('Iran'),
           plotClosure('Brazil'))

alt.VConcatChart(...)

# Relative Highest Numbers

In [42]:
# Countries with the highest new cases per million
alt.vconcat(plotClosure('Qatar'),
           plotClosure('Kuwait'),
           plotClosure('Bahrain'),
           plotClosure('Chile'),
           plotClosure('Singapore'),
           plotClosure('Peru'))

alt.VConcatChart(...)

In [21]:
import altair as alt

In [22]:
import altair as alt
from vega_datasets import data

source = data.cars()

brush = alt.selection(type='interval')

points = alt.Chart(source).mark_point().encode(
    x='Horsepower:Q',
    y='Miles_per_Gallon:Q',
    color=alt.condition(brush, 'Origin:N', alt.value('lightgray'))
).add_selection(
    brush
)

bars = alt.Chart(source).mark_bar().encode(
    y='Origin:N',
    color='Origin:N',
    x='count(Origin):Q'
).transform_filter(
    brush
)

points & bars

alt.VConcatChart(...)